In [20]:
#a bunch of import statements for the functions we'll be using
from sklearn.cluster import KMeans, AgglomerativeClustering
from scipy.cluster.hierarchy import dendrogram, linkage
from sklearn.feature_selection import SelectKBest
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics import pairwise
from sklearn.manifold import MDS

import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

import seaborn as sns
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode()

In [21]:
file = pd.read_csv("Data/onegramfilteredtfidf.csv", index_col = 0)
file.head()

1-kam-ma[1st]NU  1/2[1/2]NU  1/3[1/3]NU  10-kam-ma[10th]NU  \
id_text                                                                
c.0.1.1           0.22871         0.0         0.0                0.0   
c.0.1.2           0.00000         0.0         0.0                0.0   
c.0.2.01          0.00000         0.0         0.0                0.0   
c.0.2.02          0.00000         0.0         0.0                0.0   
c.0.2.03          0.00000         0.0         0.0                0.0   

          1000[1000]NU  100[100]NU  108000[108000]NU  1080[1080]NU  \
id_text                                                              
c.0.1.1            0.0         0.0               0.0           0.0   
c.0.1.2            0.0         0.0               0.0           0.0   
c.0.2.01           0.0         0.0               0.0           0.0   
c.0.2.02           0.0         0.0               0.0           0.0   
c.0.2.03           0.0         0.0               0.0           0.0   

          108[108]NU  10[10]NU       ...        šusi[finger]N  \
id_text                              ...                        
c.0.1.1          0.0  0.000000       ...                  0.0   
c.0.1.2          0.0  0.091941       ...                  0.0   
c.0.2.01         0.0  0.000000       ...                  0.0   
c.0.2.02         0.0  0.000000       ...                  0.0   
c.0.2.03         0.0  0.000000       ...                  0.0   

          šute?[accept]V/t  šutubur[mixture]N  šutug[reed-hut]N  \
id_text                                                           
c.0.1.1                0.0                0.0               0.0   
c.0.1.2                0.0                0.0               0.0   
c.0.2.01               0.0                0.0               0.0   
c.0.2.02               0.0                0.0               0.0   
c.0.2.03               0.0                0.0               0.0   

          šutum[storehouse]N  šutur[garment]N  šuš[cover]V/t  šu?i[barber]N  \
id_text                                                                       
c.0.1.1                  0.0              0.0            0.0            0.0   
c.0.1.2                  0.0              0.0            0.0            0.0   
c.0.2.01                 0.0              0.0            0.0            0.0   
c.0.2.02                 0.0              0.0            0.0            0.0   
c.0.2.03                 0.0              0.0            0.0            0.0   

          šu?u[stone]N  šu?ura[goose]N  
id_text                                 
c.0.1.1            0.0             0.0  
c.0.1.2            0.0             0.0  
c.0.2.01           0.0             0.0  
c.0.2.02           0.0             0.0  
c.0.2.03           0.0             0.0  

[5 rows x 4302 columns]

In [22]:
words = file.columns
texts = file.index

In [23]:
print(words[:10]) #print out the first 10 words as a sanity check
print(len(words))

Index(['1-kam-ma[1st]NU', '1/2[1/2]NU', '1/3[1/3]NU', '10-kam-ma[10th]NU',
       '1000[1000]NU', '100[100]NU', '108000[108000]NU', '1080[1080]NU',
       '108[108]NU', '10[10]NU'],
      dtype='object')
4302


In [24]:
dtm = file.as_matrix()
dtm

array([[ 0.22870994,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       ..., 
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ]])

In [25]:
len(dtm)

356

In [26]:
dist_matrix = pairwise.pairwise_distances(dtm, metric='cosine') 

pd.DataFrame(dist_matrix, index = file.index, columns = file.index).head()

id_text    c.0.1.1   c.0.1.2  c.0.2.01  c.0.2.02  c.0.2.03  c.0.2.04  \
id_text                                                                
c.0.1.1   0.000000  0.969666  0.966844  0.962367  0.997159  0.990801   
c.0.1.2   0.969666  0.000000  0.784686  0.711962  0.885036  0.692746   
c.0.2.01  0.966844  0.784686  0.000000  0.247072  0.624002  0.277678   
c.0.2.02  0.962367  0.711962  0.247072  0.000000  0.701013  0.308537   
c.0.2.03  0.997159  0.885036  0.624002  0.701013  0.000000  0.618533   

id_text   c.0.2.06  c.0.2.07  c.0.2.08  c.0.2.11    ...     c.6.1.23  \
id_text                                             ...                
c.0.1.1   0.991764  0.982808  0.983839  1.000000    ...     0.980535   
c.0.1.2   0.776205  0.983191  0.839093  0.852215    ...     0.924037   
c.0.2.01  0.788966  0.981840  0.908256  0.612501    ...     0.924557   
c.0.2.02  0.735413  0.990235  0.874896  0.598098    ...     0.909307   
c.0.2.03  0.847563  0.994129  0.953976  0.747425    ...     0.977511   

id_text   c.6.1.24  c.6.1.25  c.6.1.26  c.6.1.27  c.6.1.28   c.6.2.1  \
id_text                                                                
c.0.1.1   0.990684  0.988002  0.941854  0.986586  0.967027  0.962033   
c.0.1.2   0.991376  0.959502  0.920016  0.982423  0.932179  0.914273   
c.0.2.01  0.984093  0.958457  0.942169  0.960652  0.929098  0.888292   
c.0.2.02  0.986944  0.951509  0.950456  0.947092  0.915664  0.891771   
c.0.2.03  0.996946  0.980530  0.946146  0.985379  0.958533  0.951213   

id_text    c.6.2.2   c.6.2.3   c.6.2.5  
id_text                                 
c.0.1.1   0.953011  0.940927  0.954584  
c.0.1.2   0.919923  0.890635  0.906842  
c.0.2.01  0.904388  0.868083  0.890089  
c.0.2.02  0.908854  0.870437  0.883582  
c.0.2.03  0.987310  0.949105  0.954732  

[5 rows x 356 columns]

In [27]:
names = pd.read_csv('Data/idToTextName.csv', index_col=0, header = None)
names.columns = ["Full title"]
names.index.name = "text ref"
names["display title"] = names["Full title"].str.slice(0,23)
names.head()

Full title            display title
text ref                                                                 
c.4.12.2               A hymn to Martu (Martu B)  A hymn to Martu (Martu 
c.4.12.1           A šir-gida to Martu (Martu A)  A šir-gida to Martu (Ma
c.4.29.1           A šir-gida to Nuska (Nuska A)  A šir-gida to Nuska (Nu
c.4.29.2           A šir-gida to Nuska (Nuska B)  A šir-gida to Nuska (Nu
c.4.08.31  A balbale to Inana (Dumuzid-Inana E1)  A balbale to Inana (Dum

In [28]:
labels = names["display title"]
fulltitles = names["Full title"]
labels.head()

text ref
c.4.12.2     A hymn to Martu (Martu 
c.4.12.1     A šir-gida to Martu (Ma
c.4.29.1     A šir-gida to Nuska (Nu
c.4.29.2     A šir-gida to Nuska (Nu
c.4.08.31    A balbale to Inana (Dum
Name: display title, dtype: object

In [29]:
cluster_0 = ['c.1.4.1.3', 'c.2.4.1.7', 'c.2.4.2.14', 'c.2.4.2.26', 'c.2.4.4.1', 'c.2.4.4.2', 'c.2.4.4.3', 'c.4.07.6', 'c.4.07.7', 'c.4.07.8', 'c.4.07.9', 'c.4.08.01', 'c.4.08.02', 'c.4.08.03', 'c.4.08.04', 'c.4.08.05', 'c.4.08.07', 'c.4.08.08', 'c.4.08.18', 'c.4.08.25', 'c.4.08.26', 'c.4.08.28', 'c.4.08.29', 'c.4.08.30', 'c.4.08.32', 'c.4.08.33', 'c.4.13.02', 'c.4.22.2', 'c.5.5.5']
cluster_1 = ['c.0.1.2', 'c.0.2.01', 'c.0.2.02', 'c.0.2.03', 'c.0.2.04', 'c.0.2.06', 'c.0.2.11', 'c.0.2.13', 'c.1.6.1', 'c.1.6.2', 'c.1.6.3', 'c.2.4.2.20', 'c.2.4.4.4', 'c.2.5.4.15', 'c.2.5.7.1', 'c.4.27.01', 'c.4.27.02', 'c.4.27.03', 'c.4.27.04', 'c.4.27.07', 'c.4.80.2', 'c.5.5.4']
cluster_2 = ['c.1.3.1', 'c.1.3.2', 'c.1.3.3', 'c.1.3.4', 'c.1.3.5', 'c.1.4.1', 'c.1.4.4', 'c.1.8.1.2', 'c.1.8.2.3', 'c.2.1.6', 'c.2.4.2.24', 'c.2.4.2.a', 'c.2.5.1.3', 'c.2.5.3.1', 'c.2.5.4.10', 'c.2.5.4.11', 'c.2.5.6.4', 'c.2.6.9.8', 'c.2.7.1.1', 'c.2.8.2.6', 'c.2.8.3.1', 'c.3.3.01', 'c.3.3.10', 'c.4.07.1', 'c.4.07.2', 'c.4.07.3', 'c.4.07.4', 'c.4.07.5', 'c.4.07.a', 'c.4.08.06', 'c.4.08.09', 'c.4.08.10', 'c.4.08.16', 'c.4.08.20', 'c.4.08.a', 'c.4.19.3', 'c.4.33.2']
cluster_3 = ['c.1.1.3', 'c.1.1.4', 'c.2.1.7', 'c.2.3.1', 'c.2.3.2', 'c.2.4.1.2', 'c.2.4.1.3', 'c.2.4.1.5', 'c.2.4.1.6', 'c.2.4.1.a', 'c.2.4.2.01', 'c.2.4.2.03', 'c.2.4.2.04', 'c.2.4.2.05', 'c.2.4.2.07', 'c.2.4.2.15', 'c.2.4.2.16', 'c.2.4.2.17', 'c.2.4.2.18', 'c.2.4.2.21', 'c.2.4.2.22', 'c.2.4.2.25', 'c.2.4.4.a', 'c.2.4.5.2', 'c.2.5.1.4', 'c.2.5.2.1', 'c.2.5.3.2', 'c.2.5.3.4', 'c.2.5.4.01', 'c.2.5.4.02', 'c.2.5.4.03', 'c.2.5.4.04', 'c.2.5.4.05', 'c.2.5.4.08', 'c.2.5.4.09', 'c.2.5.4.13', 'c.2.5.4.17', 'c.2.5.4.19', 'c.2.5.4.21', 'c.2.5.4.23', 'c.2.5.4.24', 'c.2.5.4.27', 'c.2.5.4.29', 'c.2.5.4.b', 'c.2.5.5.1', 'c.2.5.5.2', 'c.2.5.5.3', 'c.2.5.5.4', 'c.2.5.5.5', 'c.2.5.6.1', 'c.2.5.6.2', 'c.2.5.6.3', 'c.2.5.6.5', 'c.2.5.6.6', 'c.2.5.7.2', 'c.2.5.8.1', 'c.2.6.6.1', 'c.2.6.6.5', 'c.2.6.7.1', 'c.2.6.9.1', 'c.2.6.9.2', 'c.2.6.9.3', 'c.2.6.9.4', 'c.2.6.9.5', 'c.2.6.9.6', 'c.2.6.9.7', 'c.2.8.2.2', 'c.2.8.2.4', 'c.2.8.3.2', 'c.2.8.3.3', 'c.2.8.3.5', 'c.2.8.3.6', 'c.2.8.5.1', 'c.3.3.21', 'c.4.01.1', 'c.4.02.1', 'c.4.03.1', 'c.4.05.1', 'c.4.12.1', 'c.4.12.2', 'c.4.14.1', 'c.4.15.2', 'c.4.15.3', 'c.4.16.1', 'c.4.19.1', 'c.4.21.1', 'c.4.22.1', 'c.4.22.4', 'c.4.22.5', 'c.4.22.6', 'c.4.24.1', 'c.4.25.1', 'c.4.25.2', 'c.4.26.1', 'c.4.27.06', 'c.4.28.1', 'c.4.29.1', 'c.4.29.2', 'c.4.31.1', 'c.4.33.1', 'c.4.80.1', 'c.4.80.4', 'c.5.3.7']
cluster_4 = ['c.0.1.1', 'c.1.7.6', 'c.1.7.7', 'c.2.5.1.2', 'c.3.1.01', 'c.3.1.02', 'c.3.1.03', 'c.3.1.04', 'c.3.1.05', 'c.3.1.06', 'c.3.1.06.1', 'c.3.1.07', 'c.3.1.08', 'c.3.1.11', 'c.3.1.11.1', 'c.3.1.13.2', 'c.3.1.15', 'c.3.1.16', 'c.3.1.17', 'c.3.1.18', 'c.3.1.19', 'c.3.1.20', 'c.3.1.21', 'c.3.2.02', 'c.3.2.03', 'c.3.2.04', 'c.3.3.04', 'c.3.3.05', 'c.3.3.08', 'c.3.3.09', 'c.3.3.11', 'c.4.08.23', 'c.4.08.31', 'c.5.3.1', 'c.5.6.3', 'c.5.6.5', 'c.6.1.18', 'c.6.1.21']
cluster_5 = ['c.2.4.2.b', 'c.2.4.4.6', 'c.2.4.5.1', 'c.2.4.5.3', 'c.2.4.5.4', 'c.2.4.5.5', 'c.2.5.3.3', 'c.2.6.2.1', 'c.2.6.2.a', 'c.2.8.2.3', 'c.3.3.22', 'c.4.13.01', 'c.4.13.03', 'c.4.13.04', 'c.4.13.05', 'c.4.13.07', 'c.4.13.08', 'c.4.13.09', 'c.4.13.10', 'c.4.13.11', 'c.4.13.12', 'c.4.13.13', 'c.4.13.14', 'c.4.13.15', 'c.4.13.a', 'c.4.13.c', 'c.4.17.1']
cluster_6 = ['c.0.2.07', 'c.0.2.08', 'c.1.1.1', 'c.1.1.2', 'c.1.2.1', 'c.1.2.2', 'c.1.4.1.1', 'c.1.4.3', 'c.1.5.1', 'c.1.7.1', 'c.1.7.3', 'c.1.7.4', 'c.1.7.8', 'c.1.8.1.1', 'c.1.8.1.3', 'c.1.8.1.4', 'c.1.8.1.5', 'c.1.8.1.5.1', 'c.1.8.2.1', 'c.1.8.2.2', 'c.1.8.2.4', 'c.2.1.1', 'c.2.1.2', 'c.2.1.3', 'c.2.1.4', 'c.2.1.5', 'c.2.2.2', 'c.2.2.3', 'c.2.2.4', 'c.2.2.5', 'c.2.2.6', 'c.2.4.1.1', 'c.2.4.1.4', 'c.2.4.2.02', 'c.2.4.3.1', 'c.2.5.4.a', 'c.2.8.2.1', 'c.2.8.5.a', 'c.2.8.5.b', 'c.3.2.05', 'c.3.3.02', 'c.3.3.03', 'c.3.3.39', 'c.4.06.1', 'c.4.08.15', 'c.4.13.06', 'c.4.14.2', 'c.4.14.3', 'c.4.16.2', 'c.4.19.2', 'c.4.23.1', 'c.4.32.2', 'c.4.32.e', 'c.4.32.f', 'c.5.1.3', 'c.5.2.4', 'c.5.2.5', 'c.5.3.2', 'c.5.3.3', 'c.5.3.5', 'c.5.3.6', 'c.5.4.11', 'c.5.4.12', 'c.5.5.1', 'c.5.5.2', 'c.5.5.3', 'c.5.5.a', 'c.5.6.1', 'c.5.7.1', 'c.5.7.2', 'c.5.9.1', 'c.5.9.2', 'c.6.1.01', 'c.6.1.02', 'c.6.1.03', 'c.6.1.04', 'c.6.1.05', 'c.6.1.07', 'c.6.1.08', 'c.6.1.09', 'c.6.1.10', 'c.6.1.11', 'c.6.1.12', 'c.6.1.13', 'c.6.1.14', 'c.6.1.15', 'c.6.1.16', 'c.6.1.17', 'c.6.1.19', 'c.6.1.22', 'c.6.1.23', 'c.6.1.24', 'c.6.1.25', 'c.6.1.26', 'c.6.1.27', 'c.6.1.28', 'c.6.2.1', 'c.6.2.2', 'c.6.2.3', 'c.6.2.5']

In [30]:
clusters = [cluster_0, cluster_1, cluster_2, cluster_3, cluster_4, cluster_5, cluster_6]

In [31]:
dict_color_cluster = { #define unique color for every cluster
    0: '#2c4ff9', #dark blue
    1: '#db0f12', #red
    2: '#000000', #black
    3: '#3FB230', #green
    4: '#ff54f9', #pink
    5: '#630AFF', #purple
    6: '#F5770D'  #orange 
}

In [32]:
mds_cluster = MDS(n_components = 2, dissimilarity="precomputed")  #use MDS
embeddings_cluster = mds_cluster.fit_transform(dist_matrix) #the points/vectors of the texts obtained by MDS
embeddings_cluster

array([[ 0.0159024 , -0.79343975],
       [ 0.30929124,  0.57779201],
       [ 0.38502259,  0.56296131],
       [ 0.40198954,  0.52788746],
       [ 0.5237078 , -0.57985784],
       [ 0.42168646,  0.59510261],
       [ 0.61032664, -0.23959547],
       [ 0.35087112, -0.71002111],
       [ 0.36747653, -0.58628854],
       [-0.17233303,  0.73485737],
       [-0.03194299,  0.64354327],
       [-0.21973462, -0.34134486],
       [ 0.16484138, -0.38069597],
       [ 0.1295834 , -0.02177603],
       [ 0.29973343, -0.22286513],
       [-0.26703946, -0.42499587],
       [ 0.00202544, -0.17056458],
       [ 0.06407636, -0.34096429],
       [ 0.03637418, -0.11549216],
       [-0.14680433, -0.33841375],
       [-0.11483535, -0.76462862],
       [ 0.02232799, -0.41741538],
       [-0.13436922, -0.27608851],
       [-0.42288589, -0.38810496],
       [-0.34833897, -0.58175706],
       [-0.35247011, -0.34482465],
       [-0.45125173, -0.45660919],
       [ 0.1562604 , -0.60146158],
       [ 0.00769502,

In [33]:
def clusterpicker(label):
    for i in range(len(clusters)):
        if label in clusters[i]:
            return i

In [34]:
plotdata = pd.DataFrame(embeddings_cluster, columns = ["x", "y"], index = file.index)
plotdata["cluster"] = [clusterpicker(i) for i in file.index]
plotdata["title"] = ["???" if i not in labels else labels[i] for i in file.index]
plotdata["fulltitle"] = [str(i) if i not in fulltitles else fulltitles[i] for i in file.index]
plotdata.head()

x         y  cluster                    title  \
id_text                                                          
c.0.1.1   0.015902 -0.793440        4  Ur III catalogue from N   
c.0.1.2   0.309291  0.577792        1  Ur III catalogue at Yal   
c.0.2.01  0.385023  0.562961        1  OB catalogue from Nibru   
c.0.2.02  0.401990  0.527887        1  OB catalogue in the Lou   
c.0.2.03  0.523708 -0.579858        1  OB catalogue from Urim    

                                 fulltitle  
id_text                                     
c.0.1.1   Ur III catalogue from Nibru (N1)  
c.0.1.2      Ur III catalogue at Yale (Y1)  
c.0.2.01      OB catalogue from Nibru (N2)  
c.0.2.02    OB catalogue in the Louvre (L)  
c.0.2.03       OB catalogue from Urim (U1)

In [35]:


data = [ dict(x=df['x'], y=df['y'], name='Cluster ' + str(name), mode='text', text = df['title'], hovertext = df['fulltitle'], marker = dict(size=10), 
             textfont=dict(
        family='sans serif',
        size=11,
        color=dict_color_cluster[name]
    ))
         for name, df in plotdata.groupby('cluster')]
layout= go.Layout(
    title= 'MDS of corpus',
    hovermode= 'closest',
    legend = dict(font = dict(size = 12)),
    width = 1200,
    height = 1050,
    xaxis= dict(
        title= 'x',
        ticklen= 5,
        zeroline= False,
        gridwidth= 2,
    ),
    yaxis=dict(
        title= 'y',
        ticklen= 5,
        gridwidth= 2,
    ),
    showlegend= True
)
fig= go.Figure(data=data, layout=layout)
py.iplot(fig)